In [103]:
# Imports

import math
import random
from random import randint
import numpy as np
import matplotlib
import matplotlib.pyplot as plt
from collections import namedtuple
from itertools import count
# from PIL import Image

import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
import torchvision.transforms as T

import requests
import json

from time import sleep

In [16]:
import cv2

In [4]:
hero = cv2.imread("./images/mainMonster.jpg")
print(hero.shape)
hero = cv2.resize(hero, (64,64))
cv2.imshow("window1",hero)
# cv2.waitKey()
# cv2.destroyAllWindows()

(1080, 1080, 3)


In [3]:
otherPlayer = cv2.imread("./images/otherMonster.jpg")
print(otherPlayer.shape)
otherPlayer = cv2.resize(otherPlayer, (64,64))
cv2.imshow("window2",otherPlayer)
# cv2.waitKey()
# cv2.destroyAllWindows()

(600, 800, 3)


In [5]:
smallFruit = cv2.imread("./images/smallFruit.png")
print(smallFruit.shape)
smallFruit = cv2.resize(smallFruit, (64,64))
cv2.imshow("window3",smallFruit)
# cv2.waitKey()
# cv2.destroyAllWindows()

(588, 880, 3)


In [6]:
bigFruit = cv2.imread("./images/bigFruit.jpg")
print(bigFruit.shape)
bigFruit = cv2.resize(bigFruit, (64,64))
cv2.imshow("window4",bigFruit)
cv2.waitKey()
cv2.destroyAllWindows()

(719, 800, 3)


In [1]:
# print(hero)

In [11]:
print(hero.shape, otherPlayer.shape, smallFruit.shape, bigFruit.shape)

(64, 64, 3) (64, 64, 3) (64, 64, 3) (64, 64, 3)


In [17]:
# Render Help Functions

def overWrite(startI, startJ, originalImage, smallImage):
    for i in range(smallImage.shape[0]):
        for j in range(smallImage.shape[1]):
            originalImage[startI + i][startJ + j] = smallImage[i][j]
    return originalImage

# def displayBoard(board, direction, ownI, ownJ):
def displayBoard(board, ownI, ownJ):
    # board is the board position matrix of size 6x9 such that player is at index [5][4] (bottom center)
    image = np.zeros((64*9, 64*9, 3), dtype = np.uint8)
    board = np.asarray(board)
    print(board)
    for i in range(board.shape[0]):
        for j in range(board.shape[1]):
            if board[i][j] == 1:
                overWrite(64*i,64*j,image,otherPlayer)
            elif board[i][j] == 2:
                overWrite(64*i,64*j,image,smallFruit)
            elif board[i][j] == 3:
                overWrite(64*i,64*j,image,bigFruit)
    overWrite(64*ownI,64*ownJ,image,hero)
    return image
    

In [155]:
# RL help functions

def getField(agentId):
    mainServer = "http://localhost:5001/checkField"
    req = {
        'agentId': agentId
    }
    resField = requests.post(mainServer, json = req)
    field = json.loads(resField.json().get("field"))
    return np.asarray(field)

def moveAgent(moveValue, agentId):
    mainServer = "http://localhost:5001/moveAgent"
    
    req = {
        "agentId": agentId,
        "action": str(moveValue)
    }
    
    res = requests.post(mainServer, json = req)
    
    reward = res.json().get("reward")
    done = res.json().get("done")
    
    return (reward, done)
    
def initializeAgent(agentId):
    mainServer = "http://localhost:5001/addAgent"
    req = {
    'agentId': agentId,
    'initial_i': randint(20,50),
    'initial_j': randint(20,50)
    }

    res = requests.post(mainServer, json = req)
    return res.json().get("done")

In [156]:
Transition = namedtuple('Transition',
                        ('state', 'action', 'next_state', 'reward'))


class ReplayMemory(object):

    def __init__(self, capacity):
        self.capacity = capacity
        self.memory = []
        self.position = 0

    def push(self, *args):
        """Saves a transition."""
        if len(self.memory) < self.capacity:
            self.memory.append(None)
        self.memory[self.position] = Transition(*args)
        self.position = (self.position + 1) % self.capacity

    def sample(self, batch_size):
        return random.sample(self.memory, batch_size)

    def __len__(self):
        return len(self.memory)

In [192]:
# DQN network
class DQN(nn.Module):

    def __init__(self, h, w, outputs):
        super(DQN, self).__init__()
#         self.conv1 = nn.Conv2d(3,1,3)
#         self.flattener = nn.Flatten(h*w)
        self.lin1 = nn.Linear(h*w, 128)
        self.lin2 = nn.Linear(128,32)
        self.lin3 = nn.Linear(32, outputs)

    def forward(self, x):
        x = torch.tensor(x, dtype = torch.float32)
#         x = self.flattener(x)
        print(x.shape)
        x = x.reshape(x.shape[0],-1)
#         x = x.reshape(1,-1)
        print(x.shape)
#         x = x.squeeze()
#         print(x.shape)
        x = F.relu(self.lin1(x))
        print(x.shape)
        x = F.relu(self.lin2(x))
        print(x.shape)
        x = F.relu(self.lin3(x))
        print(x.shape)
        return x

In [158]:
trial = DQN(9,9,5)

In [159]:
initialState = np.zeros((10,1,9,9))
# initialState
initialState = torch.tensor(initialState, dtype = torch.float32)
initialState[0]

tensor([[[0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.]]])

In [160]:
res = trial(initialState)
print(res)
print(res.max())
print(res.max(1))
print("\n\n\n")
print(res.max(1)[1])
print("\n\n\n")
# print(res.max(1)[1].view(1,1))

torch.Size([10, 1, 9, 9])
torch.Size([10, 81])
torch.Size([10, 64])
torch.Size([10, 5])
tensor([[0.0957, 0.0000, 0.0000, 0.0749, 0.0000],
        [0.0957, 0.0000, 0.0000, 0.0749, 0.0000],
        [0.0957, 0.0000, 0.0000, 0.0749, 0.0000],
        [0.0957, 0.0000, 0.0000, 0.0749, 0.0000],
        [0.0957, 0.0000, 0.0000, 0.0749, 0.0000],
        [0.0957, 0.0000, 0.0000, 0.0749, 0.0000],
        [0.0957, 0.0000, 0.0000, 0.0749, 0.0000],
        [0.0957, 0.0000, 0.0000, 0.0749, 0.0000],
        [0.0957, 0.0000, 0.0000, 0.0749, 0.0000],
        [0.0957, 0.0000, 0.0000, 0.0749, 0.0000]], grad_fn=<ReluBackward0>)
tensor(0.0957, grad_fn=<MaxBackward1>)
torch.return_types.max(
values=tensor([0.0957, 0.0957, 0.0957, 0.0957, 0.0957, 0.0957, 0.0957, 0.0957, 0.0957,
        0.0957], grad_fn=<MaxBackward0>),
indices=tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0]))




tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0])






/home/k7back/forML/lib/python3.6/site-packages/ipykernel_launcher.py:12: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  if sys.path[0] == '':


In [213]:
# def preTrainingRituals():
BATCH_SIZE = 128
GAMMA = 0.999
EPS_START = 0.9
EPS_END = 0.1
EPS_DECAY = 200
TARGET_UPDATE = 10

agentId = 123



# Get screen size so that we can initialize layers correctly based on shape
# returned from AI gym. Typical dimensions at this point are close to 3x40x90
# which is the result of a clamped and down-scaled render buffer in get_screen()
# init_screen = getField(agentId)
screen_height, screen_width = 19,19

# Get number of actions from gym action space
n_actions = 5

policy_net = DQN(screen_height, screen_width, n_actions)
target_net = DQN(screen_height, screen_width, n_actions)
target_net.load_state_dict(policy_net.state_dict())
target_net.eval()

optimizer = optim.RMSprop(policy_net.parameters())
memory = ReplayMemory(10000)


steps_done = 0


def select_action(state):
    global steps_done
    sample = random.random()
    eps_threshold = EPS_END + (EPS_START - EPS_END) * \
        math.exp(-1. * steps_done / EPS_DECAY)
    steps_done += 1
    if sample > eps_threshold:
        with torch.no_grad():
            # t.max(1) will return largest column value of each row.
            # second column on max result is index of where max element was
            # found, so we pick action with the larger expected reward.
            return policy_net(state).max(1)[1].view(1, 1)
    else:
        return torch.tensor([[random.randrange(n_actions)]], dtype=torch.long)


episode_durations = []


def plot_durations():
    plt.figure(2)
    plt.clf()
    durations_t = torch.tensor(episode_durations, dtype=torch.float)
    plt.title('Training...')
    plt.xlabel('Episode')
    plt.ylabel('Duration')
    plt.plot(durations_t.numpy())
    # Take 100 episode averages and plot them too
    if len(durations_t) >= 100:
        means = durations_t.unfold(0, 100, 1).mean(1).view(-1)
        means = torch.cat((torch.zeros(99), means))
        plt.plot(means.numpy())

    plt.pause(0.001)  # pause a bit so that plots are updated
    if is_ipython:
        display.clear_output(wait=True)
        display.display(plt.gcf())

In [214]:
def optimize_model():
    if len(memory) < BATCH_SIZE:
        return
    transitions = memory.sample(BATCH_SIZE)
#     print(transitions.shape)
    # Transpose the batch (see https://stackoverflow.com/a/19343/3343043 for
    # detailed explanation). This converts batch-array of Transitions
    # to Transition of batch-arrays.
    batch = Transition(*zip(*transitions))

    # Compute a mask of non-final states and concatenate the batch elements
    # (a final state would've been the one after which simulation ended)
    non_final_mask = torch.tensor(tuple(map(lambda s: s is not None,
                                          batch.next_state)), dtype=torch.bool)
    non_final_next_states = torch.cat([torch.unsqueeze(s,0) for s in batch.next_state
                                                if s is not None])
    print("\n\n\nHERE:\n",non_final_next_states.shape)
    state_batch = torch.cat(batch.state)
    action_batch = torch.cat(batch.action)
    reward_batch = torch.cat(batch.reward)

    # Compute Q(s_t, a) - the model computes Q(s_t), then we select the
    # columns of actions taken. These are the actions which would've been taken
    # for each batch state according to policy_net
    state_action_values = policy_net(state_batch).gather(1, action_batch)

    # Compute V(s_{t+1}) for all next states.
    # Expected values of actions for non_final_next_states are computed based
    # on the "older" target_net; selecting their best reward with max(1)[0].
    # This is merged based on the mask, such that we'll have either the expected
    # state value or 0 in case the state was final.
    next_state_values = torch.zeros(BATCH_SIZE)
    next_state_values[non_final_mask] = target_net(non_final_next_states).max(1)[0].detach()
    # Compute the expected Q values
    expected_state_action_values = (next_state_values * GAMMA) + reward_batch

    # Compute Huber loss
    loss = F.smooth_l1_loss(state_action_values, expected_state_action_values.unsqueeze(1))

    # Optimize the model
    optimizer.zero_grad()
    loss.backward()
    for param in policy_net.parameters():
        param.grad.data.clamp_(-1, 1)
    optimizer.step()

In [215]:

# print(initializeAgent(123))
# state = getField(123)
# print(state)
# action = select_action(state)
# print("\n\n\n", action)
# reward, done = moveAgent(action.item(), agentId)
# print(reward, done)


In [218]:
# preTrainingRituals()

num_episodes = 50
# agentId = 123

for i_episode in range(num_episodes):
    # Initialize the environment and state
    while initializeAgent(agentId):
        continue
#     last_screen = getField()
#     current_screen = getField()
#     state = current_screen - last_screen
    state, direction = getField(agentId)
    state = torch.tensor(state)
    direction = torch.tensor(direction)
    for t in count():
        # Select and perform an action
        state = torch.unsqueeze(state,0)
        action = select_action(state)
        a= action.item()
        print(a)
        reward, done = moveAgent(a, agentId)
        print("reward\n\n",reward)
        reward = float(reward)
        reward = torch.tensor([reward])
        
        sleep(0.5)
        # Observe new state
#         last_screen = current_screen
#         current_screen = get_screen()
        if not done:
            next_state = torch.tensor(getField(agentId))
        else:
            next_state = None

        # Store the transition in memory
        memory.push(state, action, next_state, reward)

        # Move to the next state
        state = torch.tensor(getField(agentId))

        # Perform one step of the optimization (on the target network)
        optimize_model()
        if done:
            episode_durations.append(t + 1)
#             plot_durations()
            break
    # Update the target network, copying all weights and biases in DQN
    print("\n\n\nHEREEEEE!!\n\n\n\n")
    if i_episode % TARGET_UPDATE == 0:
        target_net.load_state_dict(policy_net.state_dict())

print('Complete')
# env.render()
# env.close()
# plt.ioff()
# plt.show()

4
reward

 0.1
0
reward

 0.4
0
reward

 0.4
0
reward

 0
0
reward

 0
4
reward

 0.1
3
reward

 0.2
4
reward

 0.1
3
reward

 0.2
1
reward

 0.2
1
reward

 0.2
1
reward

 0
0
reward

 0.4
3
reward

 0.2
2
reward

 0.2


/home/k7back/forML/lib/python3.6/site-packages/ipykernel_launcher.py:13: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  del sys.path[0]


torch.Size([1, 19, 19])
torch.Size([1, 361])
torch.Size([1, 128])
torch.Size([1, 32])
torch.Size([1, 5])
2
reward

 0.2
4
reward

 0.1
3
reward

 0.2
3
reward

 0.2
torch.Size([1, 19, 19])
torch.Size([1, 361])
torch.Size([1, 128])
torch.Size([1, 32])
torch.Size([1, 5])
2
reward

 0.2
1
reward

 0.2
torch.Size([1, 19, 19])
torch.Size([1, 361])
torch.Size([1, 128])
torch.Size([1, 32])
torch.Size([1, 5])
2
reward

 0.2
torch.Size([1, 19, 19])
torch.Size([1, 361])
torch.Size([1, 128])
torch.Size([1, 32])
torch.Size([1, 5])
2
reward

 0.2
0
reward

 0.4
3
reward

 0.2
0
reward

 0.4
1
reward

 0.2
torch.Size([1, 19, 19])
torch.Size([1, 361])
torch.Size([1, 128])
torch.Size([1, 32])
torch.Size([1, 5])
2
reward

 0.2
0
reward

 0.4
4
reward

 0.1
1
reward

 0.2
3
reward

 0.2
torch.Size([1, 19, 19])
torch.Size([1, 361])
torch.Size([1, 128])
torch.Size([1, 32])
torch.Size([1, 5])
1
reward

 0.2
0
reward

 0.4
2
reward

 0.2
torch.Size([1, 19, 19])
torch.Size([1, 361])
torch.Size([1, 128])
torc




HERE:
 torch.Size([128, 19, 19])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
3
reward

 0.2



HERE:
 torch.Size([128, 19, 19])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([1, 19, 19])
torch.Size([1, 361])
torch.Size([1, 128])
torch.Size([1, 32])
torch.Size([1, 5])
3
reward

 0.2



HERE:
 torch.Size([128, 19, 19])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
4
reward

 0.1



HERE:
 torch.Size([128, 19, 19])
torch.Size([128,




HERE:
 torch.Size([128, 19, 19])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
0
reward

 0.4



HERE:
 torch.Size([128, 19, 19])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([1, 19, 19])
torch.Size([1, 361])
torch.Size([1, 128])
torch.Size([1, 32])
torch.Size([1, 5])
3
reward

 0.2



HERE:
 torch.Size([128, 19, 19])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
2
reward

 0.2



HERE:
 torch.Size([128, 19, 19])
torch.Size([128,

...




HERE:
 torch.Size([127, 19, 19])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([127, 19, 19])
torch.Size([127, 361])
torch.Size([127, 128])
torch.Size([127, 32])
torch.Size([127, 5])
torch.Size([1, 19, 19])
torch.Size([1, 361])
torch.Size([1, 128])
torch.Size([1, 32])
torch.Size([1, 5])
1
reward

 0.2



HERE:
 torch.Size([128, 19, 19])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([1, 19, 19])
torch.Size([1, 361])
torch.Size([1, 128])
torch.Size([1, 32])
torch.Size([1, 5])
1
reward

 0.2



HERE:
 torch.Size([127, 19, 19])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([127, 19, 19])
torch.Size([127, 361])
torch.Size([127, 128])
torch




HERE:
 torch.Size([126, 19, 19])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([126, 19, 19])
torch.Size([126, 361])
torch.Size([126, 128])
torch.Size([126, 32])
torch.Size([126, 5])
0
reward

 0.4



HERE:
 torch.Size([128, 19, 19])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([1, 19, 19])
torch.Size([1, 361])
torch.Size([1, 128])
torch.Size([1, 32])
torch.Size([1, 5])
0
reward

 0.4



HERE:
 torch.Size([128, 19, 19])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([1, 19, 19])
torch.Size([1, 361])
torch.Size([1, 128])
t




HERE:
 torch.Size([128, 19, 19])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([1, 19, 19])
torch.Size([1, 361])
torch.Size([1, 128])
torch.Size([1, 32])
torch.Size([1, 5])
0
reward

 0.4



HERE:
 torch.Size([127, 19, 19])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([127, 19, 19])
torch.Size([127, 361])
torch.Size([127, 128])
torch.Size([127, 32])
torch.Size([127, 5])
torch.Size([1, 19, 19])
torch.Size([1, 361])
torch.Size([1, 128])
torch.Size([1, 32])
torch.Size([1, 5])
0
reward

 0



HERE:
 torch.Size([128, 19, 19])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.S




HERE:
 torch.Size([128, 19, 19])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([1, 19, 19])
torch.Size([1, 361])
torch.Size([1, 128])
torch.Size([1, 32])
torch.Size([1, 5])
0
reward

 0.4



HERE:
 torch.Size([128, 19, 19])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
torch.Size([128, 19, 19])
torch.Size([128, 361])
torch.Size([128, 128])
torch.Size([128, 32])
torch.Size([128, 5])
4
reward

 0.1


ConnectionError: HTTPConnectionPool(host='localhost', port=5001): Max retries exceeded with url: /checkField (Caused by NewConnectionError('<requests.packages.urllib3.connection.HTTPConnection object at 0x7fbcd045b9e8>: Failed to establish a new connection: [Errno 111] Connection refused',))